In [18]:
import cv2
import os
import numpy as np
import random

# **1. 3D 회전 함수**
def rotate_3d(image, angle_x, angle_y, angle_z):
    h, w = image.shape[:2]

    # 중심점 기준으로 회전 변환 행렬 생성
    center = np.array([w / 2, h / 2, 0])

    # X축 회전 행렬
    rx = np.array([
        [1, 0, 0],
        [0, np.cos(angle_x), -np.sin(angle_x)],
        [0, np.sin(angle_x), np.cos(angle_x)],
    ])

    # Y축 회전 행렬
    ry = np.array([
        [np.cos(angle_y), 0, np.sin(angle_y)],
        [0, 1, 0],
        [-np.sin(angle_y), 0, np.cos(angle_y)],
    ])

    # Z축 회전 행렬
    rz = np.array([
        [np.cos(angle_z), -np.sin(angle_z), 0],
        [np.sin(angle_z), np.cos(angle_z), 0],
        [0, 0, 1],
    ])

    # 최종 회전 행렬
    rotation_matrix = rz @ ry @ rx

    # 회전 변환 후의 이미지 크기 계산
    points = np.array([
        [-w / 2, -h / 2, 0],
        [w / 2, -h / 2, 0],
        [w / 2, h / 2, 0],
        [-w / 2, h / 2, 0],
    ])
    rotated_points = points @ rotation_matrix.T + center

    # 새로운 투시 변환 행렬 계산
    src_pts = points[:, :2] + center[:2]
    dst_pts = rotated_points[:, :2]
    transform_matrix = cv2.getPerspectiveTransform(src_pts.astype(np.float32), dst_pts.astype(np.float32))

    # 이미지 변환
    transformed = cv2.warpPerspective(image, transform_matrix, (w, h), borderMode=cv2.BORDER_CONSTANT, borderValue=(0, 0, 0))
    return transformed

# **2. 입력 이미지 경로**
input_dir = "/home/hyun/dev_ws/ROS_project/training/position"
images = ["image1.png", "image2.png", "image3.png", "image4.png"]

# **3. 출력 디렉토리 설정**
output_dir = "3d_augmented_images"
os.makedirs(output_dir, exist_ok=True)

# **4. 3D 회전 증강**
for image_name in images:
    image_path = os.path.join(input_dir, image_name)
    image = cv2.imread(image_path)

    if image is None:
        print(f"❌ Error: Failed to read image at {image_path}")
        continue

    # 이미지당 30장 증강 생성
    for i in range(30):
        angle_x = np.radians(random.uniform(-60, 60))  # X축 회전 각도 (라디안, 제한적)
        angle_y = np.radians(random.uniform(-60, 60))  # Y축 회전 각도 (라디안, 제한적)
        angle_z = np.radians(random.uniform(-5, 5))  # Z축 회전 각도 (라디안, 강조)

        augmented = rotate_3d(image, angle_x, angle_y, angle_z)
        output_path = os.path.join(output_dir, f"{os.path.splitext(image_name)[0]}_3d_aug_{i}.png")
        cv2.imwrite(output_path, augmented)

print("✅ Z축 강조 3D 회전 증강 완료! 증강된 이미지는 '3d_augmented_images' 폴더에 저장되었습니다.")


✅ Z축 강조 3D 회전 증강 완료! 증강된 이미지는 '3d_augmented_images' 폴더에 저장되었습니다.


In [20]:
from ultralytics import YOLO

# **1. YOLOv8-Seg 모델 초기화**
model = YOLO('yolov8n-seg.pt')  # Pretrained YOLOv8-Segmentation 모델

# **2. 모델 학습**
model.train(
    data='/home/hyun/dev_ws/ROS_project/training/position/mydata/data.yaml',  # 데이터셋 구성 파일
    epochs=50,               # 학습 에포크 수
    batch=16,                # 배치 크기
    imgsz=(320, 256),        # 입력 이미지 크기 (320x256으로 설정)
    workers=4                # 데이터 로드 작업 수
)

# **3. 학습 완료 후 모델 평가**
model.val()

# **4. 학습된 모델 경로**
print("✅ 학습된 모델 경로:", model.ckpt_path)


New https://pypi.org/project/ultralytics/8.3.72 available 😃 Update with 'pip install -U ultralytics'
Ultralytics 8.3.65 🚀 Python-3.12.3 torch-2.5.1+cu124 CUDA:0 (NVIDIA GeForce RTX 2060, 5920MiB)
engine/trainer: task=segment, mode=train, model=yolov8n-seg.pt, data=/home/hyun/dev_ws/ROS_project/training/position/mydata/data.yaml, epochs=50, time=None, patience=100, batch=16, imgsz=(320, 256), save=True, save_period=-1, cache=False, device=None, workers=4, project=None, name=train2, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classe

100%|██████████| 5.35M/5.35M [00:00<00:00, 76.2MB/s]


AMP: checks passed ✅
WARNING ⚠️ updating to 'imgsz=320'. 'train' and 'val' imgsz must be an integer, while 'predict' and 'export' imgsz may be a [h, w] list or an integer, i.e. 'yolo export imgsz=640,480' or 'yolo export imgsz=640'


train: Scanning /home/hyun/dev_ws/ROS_project/training/position/mydata/train/labels... 288 images, 0 backgrounds, 0 corrupt: 100%|██████████| 288/288 [00:00<00:00, 2807.90it/s]

train: New cache created: /home/hyun/dev_ws/ROS_project/training/position/mydata/train/labels.cache
albumentations: Blur(p=0.01, blur_limit=(3, 7)), MedianBlur(p=0.01, blur_limit=(3, 7)), ToGray(p=0.01, num_output_channels=3, method='weighted_average'), CLAHE(p=0.01, clip_limit=(1.0, 4.0), tile_grid_size=(8, 8))


...


50 epochs completed in 0.039 hours.
Optimizer stripped from runs/segment/train2/weights/last.pt, 6.7MB
Optimizer stripped from runs/segment/train2/weights/best.pt, 6.7MB

Validating runs/segment/train2/weights/best.pt...
Ultralytics 8.3.65 🚀 Python-3.12.3 torch-2.5.1+cu124 CUDA:0 (NVIDIA GeForce RTX 2060, 5920MiB)
YOLOv8n-seg summary (fused): 195 layers, 3,258,844 parameters, 0 gradients, 12.0 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 1/1 [00:00<00:00,  6.68it/s]


                   all         24         24      0.989          1      0.995      0.995      0.989          1      0.995      0.974
                 black          9          9      0.997          1      0.995      0.995      0.997          1      0.995      0.984
                 green          4          4      0.984          1      0.995      0.995      0.984          1      0.995      0.964
                silver          8          8      0.992          1      0.995      0.995      0.992          1      0.995      0.995
                   sky          3          3      0.983          1      0.995      0.995      0.983          1      0.995      0.951
Speed: 0.1ms preprocess, 0.6ms inference, 0.0ms loss, 1.1ms postprocess per image
Results saved to runs/segment/train2
Ultralytics 8.3.65 🚀 Python-3.12.3 torch-2.5.1+cu124 CUDA:0 (NVIDIA GeForce RTX 2060, 5920MiB)
YOLOv8n-seg summary (fused): 195 layers, 3,258,844 parameters, 0 gradients, 12.0 GFLOPs


val: Scanning /home/hyun/dev_ws/ROS_project/training/position/mydata/valid/labels.cache... 24 images, 0 backgrounds, 0 corrupt: 100%|██████████| 24/24 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95)     Mask(P          R      mAP50  mAP50-95): 100%|██████████| 2/2 [00:00<00:00,  3.70it/s]


                   all         24         24      0.989          1      0.995      0.992      0.989          1      0.995      0.974
                 black          9          9      0.997          1      0.995      0.984      0.997          1      0.995      0.984
                 green          4          4      0.984          1      0.995      0.995      0.984          1      0.995      0.964
                silver          8          8      0.992          1      0.995      0.995      0.992          1      0.995      0.995
                   sky          3          3      0.982          1      0.995      0.995      0.982          1      0.995      0.951
Speed: 0.1ms preprocess, 9.9ms inference, 0.0ms loss, 1.5ms postprocess per image
Results saved to runs/segment/train22
✅ 학습된 모델 경로: yolov8n-seg.pt


In [1]:
import cv2
import torch
import numpy as np
from ultralytics import YOLO

# YOLO 세그멘테이션 모델 로드
model_path = "/home/hyun/dev_ws/ROS_project/training/position/src/runs/segment/train2/weights/best.pt"
model = YOLO(model_path)

# 웹캠 열기
cap = cv2.VideoCapture(0)  # 웹캠 사용
if not cap.isOpened():
    print("카메라를 열 수 없습니다. 다른 인덱스를 시도하세요.")
    for i in range(5):
        cap = cv2.VideoCapture(i)
        if cap.isOpened():
            print(f"사용 가능한 카메라: {i}")
            break

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    # YOLO 예측 수행
    results = model(frame)

    for r in results:
        print(r)  # 결과 객체 출력
        if hasattr(r, "masks") and r.masks is not None:
            for mask in r.masks.xy:  # 마스크 좌표 가져오기
                mask = np.array(mask, dtype=np.int32)
                cv2.polylines(frame, [mask], isClosed=True, color=(0, 255, 0), thickness=2)
                cv2.fillPoly(frame, [mask], color=(0, 255, 0))  # 4채널(X) → 3채널(O)

    # 화면 출력
    cv2.imshow("YOLOv8 Segmentation", frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()



0: 256x320 1 silver, 1 sky, 49.8ms
Speed: 2.3ms preprocess, 49.8ms inference, 118.1ms postprocess per image at shape (1, 3, 256, 320)
ultralytics.engine.results.Results object with attributes:

boxes: ultralytics.engine.results.Boxes object
keypoints: None
masks: ultralytics.engine.results.Masks object
names: {0: 'black', 1: 'green', 2: 'silver', 3: 'sky'}
obb: None
orig_img: array([[[179, 178, 174],
        [179, 178, 174],
        [180, 179, 175],
        ...,
        [216, 207, 208],
        [215, 206, 207],
        [215, 206, 207]],

       [[180, 178, 178],
        [180, 178, 178],
        [178, 178, 178],
        ...,
        [216, 207, 208],
        [220, 208, 210],
        [220, 208, 210]],

       [[179, 177, 177],
        [179, 177, 177],
        [179, 178, 174],
        ...,
        [216, 207, 208],
        [220, 208, 210],
        [220, 208, 210]],

       ...,

       [[118, 114, 120],
        [106, 102, 107],
        [102, 101, 106],
        ...,
        [ 36,  33,  35],

In [ ]:
import cv2
import torch
import numpy as np
from ultralytics import YOLO

# YOLO 세그멘테이션 모델 로드
model_path = "/home/hyun/dev_ws/ROS_project/training/position/src/runs/segment/train2/weights/best.pt"
model = YOLO(model_path)

# 클래스 ID를 원하는 이름으로 매핑
class_mapping = {
    0: "Window1",
    1: "Exit",
    2: "Hydrant",
    3: "Window2",
}  # 원하는 대로 추가 가능

# 웹캠 열기
cap = cv2.VideoCapture(0)  # 웹캠 사용
if not cap.isOpened():
    print("카메라를 열 수 없습니다. 다른 인덱스를 시도하세요.")
    for i in range(5):
        cap = cv2.VideoCapture(i)
        if cap.isOpened():
            print(f"사용 가능한 카메라: {i}")
            break

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    overlay = frame.copy()  # 투명도 적용을 위한 복사본 생성

    # YOLO 예측 수행
    results = model(frame)

    for r in results:
        print(r)  # 결과 객체 출력

        if hasattr(r, "masks") and r.masks is not None:
            for i, mask in enumerate(r.masks.xy):  # 마스크 좌표 가져오기
                mask = np.array(mask, dtype=np.int32)

                # 객체 클래스명 가져오기
                if hasattr(r, "boxes") and hasattr(r.boxes, "cls"):
                    class_id = int(r.boxes.cls[i])  # 클래스 ID
                    class_name = class_mapping.get(class_id, model.names[class_id] if class_id in model.names else "Unknown")
                else:
                    class_name = "Unknown"

                # 객체 영역에 반투명 효과 적용
                cv2.fillPoly(overlay, [mask], color=(0, 255, 0))  # 마스크 부분에 색칠

                # 객체 클래스명 표시 (마스크 첫 번째 점 기준)
                x, y = mask[0]
                cv2.putText(overlay, class_name, (int(x), int(y) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (0, 0, 255), 2)

    # 원본 이미지와 합성 (투명도 조절)
    alpha = 0.5  # 투명도 (0: 완전 투명, 1: 완전 불투명)
    cv2.addWeighted(overlay, alpha, frame, 1 - alpha, 0, frame)

    # 화면 출력
    cv2.imshow("YOLOv8 Segmentation (Transparent Mask)", frame)

    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()


In [ ]:
import numpy as np
import cv2
from ultralytics import YOLO

# === 📌 1. 카메라 캘리브레이션 파라미터 ===
calibration_matrix = np.array([
    [267.79650171, 0., 140.13033557],
    [0., 271.46411043, 147.62847192],
    [0., 0., 1.]
])

# 왜곡 계수 (Distortion Coefficients)
distortion_coefficients = np.array([-0.51294983, 3.29922758, -0.01057857, -0.01969346, -6.78451324])

# === 📌 2. 객체의 실제 크기 (m) ===
object_real_size = {
    "green": (0.098, 0.098),  # (너비 W_real, 높이 H_real) in meters
    "silver": (0.098, 0.136)
}

# === 📌 3. 비상구 및 소화전의 월드 좌표 (지도에서의 고정된 위치) ===
object_world_coords = {
    "green": np.array([-0.23252665996551514, -0.0031995137687772512, -0.001434326171875]),  # 비상구 (X_world, Y_world, Z_world)
    "silver": np.array([0.8195663690567017, 1.2595571279525757, 0.002471923828125])  # 소화전 (X_world, Y_world, Z_world)
}

# === 📌 4. YOLO 모델 로드 ===
model = YOLO("/home/hyun/dev_ws/ROS_project/training/position/src/runs/segment/train2/weights/best.pt")

cap = cv2.VideoCapture(0)

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    # === 📌 5. 카메라 왜곡 보정 (Undistortion) ===
    h, w = frame.shape[:2]
    new_camera_matrix, roi = cv2.getOptimalNewCameraMatrix(calibration_matrix, distortion_coefficients, (w, h), 1, (w, h))
    frame = cv2.undistort(frame, calibration_matrix, distortion_coefficients, None, new_camera_matrix)

    results = model(frame)

    for r in results:
        if hasattr(r, "masks") and r.masks is not None:
            for i, mask in enumerate(r.masks.xy):  # 마스크 좌표 가져오기
                mask = np.array(mask, dtype=np.int32)

                # 📌 6. 객체 클래스명 가져오기
                class_id = int(r.boxes.cls[i])
                class_name = model.names[class_id] if class_id in model.names else "Unknown"

                # === 📌 7. 마스크 중심점 계산 ===
                M = cv2.moments(mask)
                if M["m00"] != 0:
                    u = int(M["m10"] / M["m00"])  # X 좌표 (픽셀)
                    v = int(M["m01"] / M["m00"])  # Y 좌표 (픽셀)
                else:
                    continue

                # === 📌 8. 거리(Z) 계산 (객체 크기 기반) ===
                if class_name in object_real_size:
                    W_real, H_real = object_real_size[class_name]
                    Z = (calibration_matrix[1, 1] * H_real) / cv2.boundingRect(mask)[3]  # 객체 높이 이용

                    # 📌 9. 픽셀 좌표 → 카메라 좌표 변환
                    pixel_coords = np.array([u, v, 1])
                    cam_coords = Z * np.linalg.inv(calibration_matrix) @ pixel_coords
                    X_cam, Y_cam, Z_cam = cam_coords.flatten()

                    # 📌 10. 카메라 좌표 → 월드 좌표 변환
                    if class_name in object_world_coords:
                        X_obj, Y_obj, Z_obj = object_world_coords[class_name]

                        # 로봇 위치 보정 (객체의 월드 좌표를 기준으로 로봇 상대 위치 계산)
                        X_robot = X_obj - X_cam
                        Y_robot = Y_obj - Y_cam
                        Z_robot = Z_obj - Z_cam

                        # 📌 11. 마스크 방향성 분석 (PCA 기반 방향 벡터) ===
                        mean, eigenvectors = cv2.PCACompute(mask.astype(np.float32), mean=None)
                        yaw_angle = np.arctan2(eigenvectors[0, 1], eigenvectors[0, 0])  # 주축 방향 (라디안)

                        # 📌 12. Yaw → Z, W 변환 (수정된 공식 적용)
                        Z = np.sin(yaw_angle) # -1 ~ 1
                        W = np.cos(yaw_angle)  # 0 ~ 1

                        # 📌 13. 결과 출력
                        print(f"🔹 로봇 위치 보정: X={X_robot:.2f}, Y={Y_robot:.2f}, Z={Z_robot:.2f}, Z={Z:.4f}, W={W:.4f}")

                        # === 📌 14. 마스크 시각화 ===
                        cv2.polylines(frame, [mask], isClosed=True, color=(0, 255, 0), thickness=2)
                        cv2.putText(frame, f"{class_name} (Z: {Z:.4f}, W: {W:.4f})", 
                                    (int(u), int(v) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (0, 0, 255), 2)

    cv2.imshow("YOLOv8 Segmentation (Mask-based Orientation)", frame)
    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()



0: 256x320 (no detections), 48.5ms
Speed: 4.9ms preprocess, 48.5ms inference, 32.7ms postprocess per image at shape (1, 3, 256, 320)

0: 256x320 (no detections), 7.3ms
Speed: 1.1ms preprocess, 7.3ms inference, 0.4ms postprocess per image at shape (1, 3, 256, 320)

0: 256x320 1 sky, 8.8ms
Speed: 1.2ms preprocess, 8.8ms inference, 115.9ms postprocess per image at shape (1, 3, 256, 320)

0: 256x320 1 sky, 9.4ms
Speed: 0.9ms preprocess, 9.4ms inference, 2.9ms postprocess per image at shape (1, 3, 256, 320)

0: 256x320 1 sky, 7.4ms
Speed: 1.1ms preprocess, 7.4ms inference, 24.9ms postprocess per image at shape (1, 3, 256, 320)

0: 256x320 (no detections), 6.3ms
Speed: 1.2ms preprocess, 6.3ms inference, 0.4ms postprocess per image at shape (1, 3, 256, 320)

0: 256x320 (no detections), 7.9ms
Speed: 1.2ms preprocess, 7.9ms inference, 0.5ms postprocess per image at shape (1, 3, 256, 320)

0: 256x320 (no detections), 7.4ms
Speed: 1.2ms preprocess, 7.4ms inference, 0.4ms postprocess per image at